In [1]:
import pandas as pd
import numpy as np
import pdb, os
from tqdm import tqdm

In [2]:
#study_data_path = '../IntentData/'
#data = pd.read_pickle(study_data_path + "/Preprocessing_data/filtered_data.pkl")
data = pd.read_pickle("filtered_data.pkl")

# Nine events (1 underdefined included)
data[(data.type == "toolbar")].groupby(["event"]).count()

level_0  Timestamp  type   PID  key  data  range  \
event                                                                           
 undefined                         2          2     2     2    0     0      0   
Align centerAlign                498        498   498   498    0     0      0   
Align leftAlign                   52         52    52    52    0     0      0   
Align rightAlign                 436        436   436   436    0     0      0   
Bold (CTRL+B)Bold                338        338   338   338    0     0      0   
Font FamilyFont                 3058       3058  3058  3058    0     0      0   
Font SizeFont                   1558       1558  1558  1558    0     0      0   
Italic (CTRL+I)Italic            349        349   349   349    0     0      0   
Underline (CTRL+U)Underline      396        396   396   396    0     0      0   

                             index  Left_Gaze_X  Left_Gaze_Y  ...  clientY  \
event                                                         ...            
 undefined                       0            0            0  ...        0   
Align centerAlign                0            0            0  ...        0   
Align leftAlign                  0            0            0  ...        0   
Align rightAlign                 0            0            0  ...        0   
Bold (CTRL+B)Bold                0            0            0  ...        0   
Font FamilyFont                  0            0            0  ...        0   
Font SizeFont                    0            0            0  ...        0   
Italic (CTRL+I)Italic            0            0            0  ...        0   
Underline (CTRL+U)Underline      0            0            0  ...        0   

                             condition  part  taskID  button  \
event                                                          
 undefined                           2     2       2       0   
Align centerAlign                  498   498     498       0   
Align leftAlign                     52    52      52       0   
Align rightAlign                   436   436     436       0   
Bold (CTRL+B)Bold                  338   338     338       0   
Font FamilyFont                   3058  3058    3058       0   
Font SizeFont                     1558  1558    1558       0   
Italic (CTRL+I)Italic              349   349     349       0   
Underline (CTRL+U)Underline        396   396     396       0   

                             isCurrentlyPasting  lorem_format  lorem_text  \
event                                                                       
 undefined                                    0             0           0   
Align centerAlign                             0             0           0   
Align leftAlign                               0             0           0   
Align rightAlign                              0             0           0   
Bold (CTRL+B)Bold                             0             0           0   
Font FamilyFont                               0             0           0   
Font SizeFont                                 0             0           0   
Italic (CTRL+I)Italic                         0             0           0   
Underline (CTRL+U)Underline                   0             0           0   

                             rules  label  
event                                      
 undefined                       2      2  
Align centerAlign              498    498  
Align leftAlign                 52     52  
Align rightAlign               436    436  
Bold (CTRL+B)Bold              338    338  
Font FamilyFont               3058   3058  
Font SizeFont                 1558   1558  
Italic (CTRL+I)Italic          349    349  
Underline (CTRL+U)Underline    396    396  

[9 rows x 27 columns]

In [3]:
# Remove samples where rules=None
data = data[(data.rules != 'None')]

action_array = data[(data.type == "commands") | (data.type == "toolbar")].event.unique()
action_array

array(['Tab', 'Ctrl+I', 'Ctrl+Z', 'Esc', 'Italic (CTRL+I)Italic',
       'Font FamilyFont', 'Ctrl+B', 'Align centerAlign', 'Font SizeFont',
       'Align rightAlign', 'Underline (CTRL+U)Underline', nan, 'Ctrl+C',
       'Shift+Tab', 'Bold (CTRL+B)Bold', ' undefined', 'Ctrl+A',
       'Align leftAlign', 'Ctrl+N', 'Ctrl+V', 'Ctrl+H', 'Ctrl+Y',
       'Ctrl+S', 'Ctrl+Tab', 'Ctrl+7'], dtype=object)

In [4]:
toolbar_list = ['Bold (CTRL+B)Bold',
                'Italic (CTRL+I)Italic',
                'Underline (CTRL+U)Underline',
                'Font SizeFont',
                'Font FamilyFont',
                'Align leftAlign',
                'Align centerAlign',
                'Align rightAlign',
                'undefined']
''''command_list = ['Ctrl+B',
                'Ctrl+I',
                'Tab',
                'Shift+Tab',
                'Ctrl+C',
                'Ctrl+V',
                'Ctrl+Z']'''
allowed_command_list = ['Ctrl+B',
                'Ctrl+I',
                'Tab',
                'Shift+Tab',
                'Ctrl+U'] # As written in the paper, only allowed these shortcuts
action_list = ['Bold', 
               'Italic', 
               'Underline',
               'FontSize',
               'FontFamily',
               'AlignmentLeft',
               'AlignmentCenter',
               'AlignmentRight',
               'Indent']
# Map the keyboard shortcuts and operations on the toolbar to actions
# 'Bold' 0
# 'Italic' 1
# 'Underline' 2
# 'Font Size' 3
# 'Font Family' 4
# 'Alignment center' 5
# 'Alignment right' 6
# 'Alignment left' 7
# 'Indent' 8
# 'Revert' 9 
# 'Next Task' 10
# 'Copy' 11 
# 'nan/undefined' 12
action_numbers = [8, 1, 9, 10, 1, 4, 0, 5, 3, 6, 2, 12, 11, 8, 0, 12]
action_dict = dict(zip(action_array, action_numbers))
action_dict

{'Tab': 8,
 'Ctrl+I': 1,
 'Ctrl+Z': 9,
 'Esc': 10,
 'Italic (CTRL+I)Italic': 1,
 'Font FamilyFont': 4,
 'Ctrl+B': 0,
 'Align centerAlign': 5,
 'Font SizeFont': 3,
 'Align rightAlign': 6,
 'Underline (CTRL+U)Underline': 2,
 nan: 12,
 'Ctrl+C': 11,
 'Shift+Tab': 8,
 'Bold (CTRL+B)Bold': 0,
 ' undefined': 12}

In [5]:
data.type.unique()

array(['commands', 'key', 'selection', 'toolbar', 'eye', 'pos', 'click',
       'start', 'end', 'lorem'], dtype=object)

In [6]:
# Take out dataframes
df_keys = data[data.type == "key"]
df_eyes = data[data.type == "eye"]
df_mouse_pos = data[data.type == "pos"]
df_mouse_click = data[data.type == "click"]
df_mouses = pd.concat([df_mouse_pos, df_mouse_click])
df_cmds = data[data.type == "commands"]
df_toolbars = data[data.type == "toolbar"]
print("keys:", len(df_keys), "\neyes:", len(df_eyes), "\nmouse:", len(df_mouses), "\ncmd:",len(df_cmds), "\ntoolbar:",len(df_toolbars))

keys: 34407 
eyes: 8106054 
mouse: 1947827 
cmd: 3459 
toolbar: 6859


In [7]:
# Only take needed columns
df_key = pd.DataFrame({"Timestamp": df_keys.Timestamp, 
                       "Event": df_keys.event, 
                       "Key": df_keys.key,
                       "TaskID": df_keys.taskID,
                       "Part": df_keys.part, 
                       "PID": df_keys.PID,
                       "TextRule": df_keys.rules,
                       "Rule": df_keys.label})
df_eye = pd.DataFrame({"Timestamp": df_eyes.Timestamp, 
                       "Gaze_X": df_eyes.Gaze_X, 
                       "Gaze_Y": df_eyes.Gaze_Y, 
                       "TaskID": df_eyes.taskID,
                       "Part": df_eyes.part, 
                       "PID": df_eyes.PID,
                       "TextRule": df_eyes.rules,
                       "Rule": df_eyes.label})
df_mouse = pd.DataFrame({"Timestamp": df_mouses.Timestamp, 
                         "X": df_mouses.clientX, 
                         "Y": df_mouses.clientY,
                         "Type": df_mouses.type, 
                         "TaskID": df_mouses.taskID,
                         "Part": df_mouses.part, 
                         "PID": df_mouses.PID,
                         "TextRule": df_mouses.rules,
                         "Event": df_mouses.event,
                         "Rule": df_mouses.label})
df_mousePos = pd.DataFrame({"Timestamp": df_mouse_pos.Timestamp, 
                         "X": df_mouse_pos.clientX, 
                         "Y": df_mouse_pos.clientY,
                         "Type": df_mouse_pos.type, 
                         "TaskID": df_mouse_pos.taskID,
                         "Part": df_mouse_pos.part, 
                         "PID": df_mouse_pos.PID,
                         "TextRule": df_mouse_pos.rules,
                         "Rule": df_mouse_pos.label})
df_cmd = pd.DataFrame({"Timestamp": df_cmds.Timestamp, 
                       "Event": df_cmds.event, 
                       "TaskID": df_cmds.taskID,
                       "Part": df_cmds.part, 
                       "PID": df_cmds.PID,
                       "TextRule": df_cmds.rules,
                       "Rule": df_cmds.label})
df_toolbar = pd.DataFrame({"Timestamp": df_toolbars.Timestamp, 
                       "Event": df_toolbars.event, 
                       "TaskID": df_toolbars.taskID,
                       "Part": df_toolbars.part, 
                       "PID": df_toolbars.PID,
                       "TextRule": df_toolbars.rules,
                       "Rule": df_toolbars.label})
# Keep PID, Part, TaskID, TextRule and Rule. Add Gaze and Pos
df_label = df_eye.groupby(["PID","Part","TaskID"]).count().reset_index().drop(["Timestamp", "Gaze_X", "Gaze_Y"], axis=1)
df_label["Gaze"] = 0
df_label["Pos"] = 0
#print(df_label)

# Change keyboard values to uppercase
df_key.Key = df_key.Key.apply(lambda x: x.upper())

In [8]:
# All events for 'ESCAPE' are keydown !!!!!!
df_key[df_key.Key=='ESCAPE']

Timestamp    Event     Key  TaskID  Part  PID  \
91      1575388456995  keydown  ESCAPE       0     1    1   
115894  1575388801164  keydown  ESCAPE       5     1    1   
135036  1575388888708  keydown  ESCAPE       6     1    1   
303198  1575389414398  keydown  ESCAPE       6     2    1   
371058  1575389612671  keydown  ESCAPE       2     3    1   
388604  1575389680615  keydown  ESCAPE       3     3    1   
434069  1575389811028  keydown  ESCAPE       5     3    1   
148303  1575983493827  keydown  ESCAPE       6     1    2   
209686  1575983764051  keydown  ESCAPE       2     2    2   
235155  1575983852406  keydown  ESCAPE       3     2    2   
261659  1575983923344  keydown  ESCAPE       4     2    2   
318427  1575984168751  keydown  ESCAPE       0     3    2   
339470  1575984281075  keydown  ESCAPE       1     3    2   
372164  1575984373613  keydown  ESCAPE       2     3    2   
396779  1575984444888  keydown  ESCAPE       3     3    2   
418812  1575984507738  keydown  ESCAPE       4     3    2   
456387  1575984630149  keydown  ESCAPE       6     3    2   
522249  1575984892276  keydown  ESCAPE       2     4    2   
614390  1575985243792  keydown  ESCAPE       0     5    2   
650474  1575985354507  keydown  ESCAPE       2     5    2   
666261  1575985448687  keydown  ESCAPE       3     5    2   
694249  1575985497666  keydown  ESCAPE       4     5    2   
708279  1575985549757  keydown  ESCAPE       5     5    2   
87      1576500820142  keydown  ESCAPE       0     1    3   
18630   1576500895888  keydown  ESCAPE       1     1    3   
117934  1576501236105  keydown  ESCAPE       6     1    3   
137768  1576501303236  keydown  ESCAPE       0     2    3   
174630  1576501417687  keydown  ESCAPE       2     2    3   
328371  1576501894917  keydown  ESCAPE       4     3    3   
344882  1576501949469  keydown  ESCAPE       5     3    3   
478607  1576502364010  keydown  ESCAPE       6     4    3   
531642  1576502533703  keydown  ESCAPE       2     5    3   
585677  1576502711019  keydown  ESCAPE       5     5    3   
52862   1576508583224  keydown  ESCAPE       2     1    4   
76182   1576508676858  keydown  ESCAPE       3     1    4   
114775  1576508829687  keydown  ESCAPE       5     1    4   
130820  1576508910256  keydown  ESCAPE       6     1    4   
208743  1576509229027  keydown  ESCAPE       3     2    4   
224367  1576509290491  keydown  ESCAPE       4     2    4   
271760  1576509510395  keydown  ESCAPE       0     3    4   
284662  1576509692400  keydown  ESCAPE       3     3    4   
288600  1576509746972  keydown  ESCAPE       4     3    4   
293106  1576509806032  keydown  ESCAPE       5     3    4   
299094  1576509876765  keydown  ESCAPE       6     3    4   
319972  1576510098343  keydown  ESCAPE       2     4    4   
399672  1576510384286  keydown  ESCAPE       6     4    4   
473564  1576510632190  keydown  ESCAPE       3     5    4   
511257  1576510763377  keydown  ESCAPE       5     5    4   
257     1602506765679  keydown  ESCAPE       0     1    5   
104590  1603451016010  keydown  ESCAPE       5     1   12   
246174  1603451554880  keydown  ESCAPE       5     2   12   
384072  1603452064761  keydown  ESCAPE       5     3   12   
504347  1603460189671  keydown  ESCAPE       5     4   13   
516149  1603889725164  keydown  ESCAPE       6     4   15   
259189  1603895855723  keydown  ESCAPE       4     2   16   

                                                 TextRule  Rule  
91      {'Title': ['1', 'Indent', 'and', 'Italic'], 'S...     3  
115894  {'Title': ['Size', 'Big', 'and', 'Underline'],...     1  
135036  {'Title': ['Font', 'Family', 'Consolas', 'and'...     6  
303198  {'Title': ['Font', 'Family', 'Consolas', 'and'...     6  
371058  {'Title': ['Alignment', 'Center', 'and', 'Unde...     0  
388604  {'Title': ['Size', 'Big'], 'Subtitle': ['Bold'...     5  
434069  {'Title': ['Size', 'Big', 'and', 'Underline'],...     1  
148303  {'Title': ['Bold', 'and', 'Underline'], 'Subti...     2  
2

In [9]:
# Consecutive multiple key up and down events -> only keep the first one
def detect_duplicate(row, dup, direction):
    v = 1 if (row.Key == dup) & (row.Event == direction) else 0
    return v
for dup in df_key.Key.unique():
    for direction in ["keydown", "keyup"]:
        df_key["Error_detection"] = 0
        df_key["Error_detection_id"] = 0
        # Mark all samples with dup as the value of key
        df_key.loc[df_key.Key == dup, "Error_detection"] = df_key.loc[df_key.Key == dup].apply(lambda row: detect_duplicate(row, dup, direction), axis=1)
        # Mark all samples after the first one in a consecutive segment
        df_key.loc[df_key.Key == dup, "Error_detection_id"] = df_key.loc[df_key.Key == dup, "Error_detection"].diff()
        # And remove them
        print(dup , direction, "pre: ", len(df_key.loc[df_key.Key == dup]))
        df_key = df_key[~((df_key.Key == dup) & (df_key.Event == direction) & ( df_key.Error_detection_id == 0))]
        print(dup , direction, "post: ", len(df_key.loc[df_key.Key == dup]))

ENTER keydown pre:  12480
ENTER keydown post:  12480
ENTER keyup pre:  12480
ENTER keyup post:  12480
TAB keydown pre:  2738
TAB keydown post:  2738
TAB keyup pre:  2738
TAB keyup post:  2738
CONTROL keydown pre:  8256
CONTROL keydown post:  5716
CONTROL keyup pre:  5716
CONTROL keyup post:  5712
I keydown pre:  1770
I keydown post:  1770
I keyup pre:  1770
I keyup post:  1770
Z keydown pre:  210
Z keydown post:  210
Z keyup pre:  210
Z keyup post:  210
CAPSLOCK keydown pre:  20
CAPSLOCK keydown post:  20
CAPSLOCK keyup pre:  20
CAPSLOCK keyup post:  20
SHIFT keydown pre:  394
SHIFT keydown post:  222
SHIFT keyup pre:  222
SHIFT keyup post:  222
ARROWRIGHT keydown pre:  642
ARROWRIGHT keydown post:  616
ARROWRIGHT keyup pre:  616
ARROWRIGHT keyup post:  616
ESCAPE keydown pre:  55
ESCAPE keydown post:  1
ESCAPE keyup pre:  1
ESCAPE keyup post:  1
B keydown pre:  1982
B keydown post:  1982
B keyup pre:  1982
B keyup post:  1982
U keydown pre:  1722
U keydown post:  1722
U keyup pre:  17

In [10]:
df_key.reset_index(drop=True, inplace=True)

for k in df_key.Key.unique():
    k_downs = df_key[(df_key.Key == k) & (df_key.Event == "keydown")].index.tolist()
    k_ups = df_key[(df_key.Key == k) & (df_key.Event == "keyup")].index.tolist()
    print(k, "down: " ,len(k_downs))
    print(k, "up: ",len(k_ups))
    if k!='ESCAPE':
        print(k)
        assert len(k_downs)==len(k_ups)

ENTER down:  6240
ENTER up:  6240
ENTER
TAB down:  1369
TAB up:  1369
TAB
CONTROL down:  2856
CONTROL up:  2856
CONTROL
I down:  885
I up:  885
I
Z down:  105
Z up:  105
Z
CAPSLOCK down:  10
CAPSLOCK up:  10
CAPSLOCK
SHIFT down:  111
SHIFT up:  111
SHIFT
ARROWRIGHT down:  308
ARROWRIGHT up:  308
ARROWRIGHT
ESCAPE down:  1
ESCAPE up:  0
B down:  991
B up:  991
B
U down:  861
U up:  861
U
ARROWLEFT down:  79
ARROWLEFT up:  79
ARROWLEFT
UNIDENTIFIED down:  5
UNIDENTIFIED up:  5
UNIDENTIFIED
Q down:  2
Q up:  2
Q
BACKSPACE down:  1700
BACKSPACE up:  1700
BACKSPACE
HOME down:  15
HOME up:  15
HOME
DELETE down:  52
DELETE up:  52
DELETE
ARROWUP down:  36
ARROWUP up:  36
ARROWUP
C down:  3
C up:  3
C
+ down:  1
+ up:  1
+
ARROWDOWN down:  55
ARROWDOWN up:  55
ARROWDOWN
END down:  4
END up:  4
END
A down:  10
A up:  10
A
N down:  2
N up:  2
N
V down:  9
V up:  9
V
  down:  4
  up:  4
 
. down:  16
. up:  16
.
S down:  5
S up:  5
S
ALT down:  1
ALT up:  1
ALT
D down:  4
D up:  4
D
E down:  1
E 

In [11]:
# append ctrl+u to df_cmd as it is not registered
Ctrl_downs = df_key[(df_key.Key == "CONTROL") & (df_key.Event == "keydown")].index.tolist()
Ctrl_ups = df_key[(df_key.Key == "CONTROL") & (df_key.Event == "keyup")].index.tolist()
df_cmd_u = pd.DataFrame()
for s,e in zip(Ctrl_downs, Ctrl_ups):
    tmp = df_key.loc[s:e]
    tmp = tmp[(tmp.Event == "keydown") & (tmp.Key == "U")]
    if (len(tmp) > 0):
        tmp_dict = {"Timestamp": tmp.Timestamp.iloc[0], 
                                   "Event": "Ctrl+U", 
                                   "TaskID": tmp.TaskID.iloc[0], 
                                   "Part": tmp.Part.iloc[0], 
                                   "PID":tmp.PID.iloc[0], 
                                   "TextRule":tmp.TextRule.iloc[0], 
                                   "Rule":tmp.Rule.iloc[0]}
        df_cmd_u = df_cmd_u.append(tmp_dict, ignore_index=True)        
df_cmd = df_cmd.append(df_cmd_u)

/tmp/ipykernel_625665/1936093847.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_cmd_u = df_cmd_u.append(tmp_dict, ignore_index=True)
/tmp/ipykernel_625665/1936093847.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_cmd_u = df_cmd_u.append(tmp_dict, ignore_index=True)
/tmp/ipykernel_625665/1936093847.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_cmd_u = df_cmd_u.append(tmp_dict, ignore_index=True)
/tmp/ipykernel_625665/1936093847.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_cmd_u = df_cmd_u.append(tmp_dict, ignore_index=True)
/tmp/ipykernel_625665/1936093847.py:16: FutureWarning: The frame.append meth

/tmp/ipykernel_625665/1936093847.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_cmd_u = df_cmd_u.append(tmp_dict, ignore_index=True)
/tmp/ipykernel_625665/1936093847.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_cmd_u = df_cmd_u.append(tmp_dict, ignore_index=True)
/tmp/ipykernel_625665/1936093847.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_cmd_u = df_cmd_u.append(tmp_dict, ignore_index=True)
/tmp/ipykernel_625665/1936093847.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_cmd_u = df_cmd_u.append(tmp_dict, ignore_index=True)
/tmp/ipykernel_625665/1936093847.py:16: FutureWarning: The frame.append meth

/tmp/ipykernel_625665/1936093847.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_cmd_u = df_cmd_u.append(tmp_dict, ignore_index=True)
/tmp/ipykernel_625665/1936093847.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_cmd_u = df_cmd_u.append(tmp_dict, ignore_index=True)
/tmp/ipykernel_625665/1936093847.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_cmd_u = df_cmd_u.append(tmp_dict, ignore_index=True)
/tmp/ipykernel_625665/1936093847.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_cmd_u = df_cmd_u.append(tmp_dict, ignore_index=True)
/tmp/ipykernel_625665/1936093847.py:16: FutureWarning: The frame.append meth

/tmp/ipykernel_625665/1936093847.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_cmd_u = df_cmd_u.append(tmp_dict, ignore_index=True)
/tmp/ipykernel_625665/1936093847.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_cmd_u = df_cmd_u.append(tmp_dict, ignore_index=True)
/tmp/ipykernel_625665/1936093847.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_cmd_u = df_cmd_u.append(tmp_dict, ignore_index=True)
/tmp/ipykernel_625665/1936093847.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_cmd_u = df_cmd_u.append(tmp_dict, ignore_index=True)
/tmp/ipykernel_625665/1936093847.py:16: FutureWarning: The frame.append meth

/tmp/ipykernel_625665/1936093847.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_cmd_u = df_cmd_u.append(tmp_dict, ignore_index=True)
/tmp/ipykernel_625665/1936093847.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_cmd_u = df_cmd_u.append(tmp_dict, ignore_index=True)
/tmp/ipykernel_625665/1936093847.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_cmd_u = df_cmd_u.append(tmp_dict, ignore_index=True)
/tmp/ipykernel_625665/1936093847.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_cmd_u = df_cmd_u.append(tmp_dict, ignore_index=True)
/tmp/ipykernel_625665/1936093847.py:16: FutureWarning: The frame.append meth

/tmp/ipykernel_625665/1936093847.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_cmd_u = df_cmd_u.append(tmp_dict, ignore_index=True)
/tmp/ipykernel_625665/1936093847.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_cmd_u = df_cmd_u.append(tmp_dict, ignore_index=True)
/tmp/ipykernel_625665/1936093847.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_cmd_u = df_cmd_u.append(tmp_dict, ignore_index=True)
/tmp/ipykernel_625665/1936093847.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_cmd_u = df_cmd_u.append(tmp_dict, ignore_index=True)
/tmp/ipykernel_625665/1936093847.py:16: FutureWarning: The frame.append meth

/tmp/ipykernel_625665/1936093847.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_cmd_u = df_cmd_u.append(tmp_dict, ignore_index=True)
/tmp/ipykernel_625665/1936093847.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_cmd_u = df_cmd_u.append(tmp_dict, ignore_index=True)
/tmp/ipykernel_625665/1936093847.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_cmd_u = df_cmd_u.append(tmp_dict, ignore_index=True)
/tmp/ipykernel_625665/1936093847.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_cmd_u = df_cmd_u.append(tmp_dict, ignore_index=True)
/tmp/ipykernel_625665/1936093847.py:16: FutureWarning: The frame.append meth

/tmp/ipykernel_625665/1936093847.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_cmd_u = df_cmd_u.append(tmp_dict, ignore_index=True)
/tmp/ipykernel_625665/1936093847.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_cmd_u = df_cmd_u.append(tmp_dict, ignore_index=True)
/tmp/ipykernel_625665/1936093847.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_cmd_u = df_cmd_u.append(tmp_dict, ignore_index=True)
/tmp/ipykernel_625665/1936093847.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_cmd_u = df_cmd_u.append(tmp_dict, ignore_index=True)
/tmp/ipykernel_625665/1936093847.py:16: FutureWarning: The frame.append meth

In [12]:
df_cmd.groupby(["Event"]).count()

Timestamp  TaskID  Part   PID  TextRule  Rule
Event                                                   
Ctrl+7             1       1     1     1         1     1
Ctrl+A             8       8     8     8         8     8
Ctrl+B           991     991   991   991       991   991
Ctrl+C             1       1     1     1         1     1
Ctrl+H             2       2     2     2         2     2
Ctrl+I           884     884   884   884       884   884
Ctrl+N             1       1     1     1         1     1
Ctrl+S             2       2     2     2         2     2
Ctrl+Tab           1       1     1     1         1     1
Ctrl+U           854     854   854   854       854   854
Ctrl+V             7       7     7     7         7     7
Ctrl+Y            32      32    32    32        32    32
Ctrl+Z           104     104   104   104       104   104
Esc               57      57    57    57        57    57
Shift+Tab         15      15    15    15        15    15
Tab             1353    1353  1353  1353      1353  1353

In [13]:
df_cmd.Event.unique()

array(['Tab', 'Ctrl+I', 'Ctrl+Z', 'Esc', 'Ctrl+B', 'Ctrl+C', 'Shift+Tab',
       'Ctrl+A', 'Ctrl+N', 'Ctrl+V', 'Ctrl+H', 'Ctrl+Y', 'Ctrl+S',
       'Ctrl+Tab', 'Ctrl+7', 'Ctrl+U'], dtype=object)

In [14]:
df_toolbar = df_toolbar[~df_toolbar.Event.isna()]
toolbar_array = sorted(df_toolbar.Event.unique())
toolbar_array

[' undefined',
 'Align centerAlign',
 'Align leftAlign',
 'Align rightAlign',
 'Bold (CTRL+B)Bold',
 'Font FamilyFont',
 'Font SizeFont',
 'Italic (CTRL+I)Italic',
 'Underline (CTRL+U)Underline']

In [15]:
#if not os.path.exists("../ReRun/df_mouse.pkl"):
if not os.path.exists("df_mouse.pkl"):
    df_mouse["Keep"] = 0
    df_toolbar["X"] = 0
    df_toolbar["Y"] = 0
    # Font Family: all timestamps of event FamilyFont should have ONE corresponding (within 20ms) mouse click event
    for time in tqdm(df_toolbar[df_toolbar.Event == "Font FamilyFont"].Timestamp.values):
        assert len(df_mouse[(df_mouse.Event == "up") & (df_mouse.Type == "click") & (df_mouse.Timestamp <= time + 20) & (df_mouse.Timestamp >= time - 20)]) == 1 
        df_toolbar.loc[(df_toolbar.Timestamp == time) & (df_toolbar.Event == "Font FamilyFont"), "X"] = df_mouse[(df_mouse.Event == "up") & (df_mouse.Type == "click") & (df_mouse.Timestamp <= time + 20) & (df_mouse.Timestamp >= time - 20)].X.iloc[0]
        df_toolbar.loc[(df_toolbar.Timestamp == time) & (df_toolbar.Event == "Font FamilyFont"), "Y"] = df_mouse[(df_mouse.Event == "up") & (df_mouse.Type == "click") & (df_mouse.Timestamp <= time + 20) & (df_mouse.Timestamp >= time - 20)].Y.iloc[0]
        df_mouse.loc[(df_mouse.Event == "up") & (df_mouse.Type == "click") & (df_mouse.Timestamp <= time + 20) & (df_mouse.Timestamp >= time - 20), "Keep"] = 1
    #df_mouse.to_pickle("../ReRun/df_mouse.pkl")
    #df_toolbar.to_pickle("../ReRun/df_toolbar.pkl")
    df_mouse.to_pickle("df_mouse.pkl")
    df_toolbar.to_pickle("df_toolbar.pkl")
else:
    #df_mouse = pd.read_pickle("../ReRun/df_mouse.pkl")
    #df_toolbar = pd.read_pickle("../ReRun/df_toolbar.pkl")
    df_mouse = pd.read_pickle("df_mouse.pkl")
    df_toolbar = pd.read_pickle("df_toolbar.pkl")

100%|████████████████████████████████████████████| 3058/3058 [20:03<00:00,  2.55it/s]


In [20]:
df_toolbar.reset_index(drop=True, inplace=True)
# Find the last "Font FamilyFont" in consecutive multiple "Font FamilyFont"s
''''found = False
indexes = []
for i, l in enumerate(df_toolbar.Event.tolist() + ['ENDE']):
    #print(i, l, found)
    if l in 'Font FamilyFont':
        ind = i
        found = True
    elif l not in 'Font FamilyFont' and found:
        indexes.append(ind)
        found = False
    elif l in 'Font FamilyFont' and found:
        indexes.append(i)
print(indexes)
len(indexes)'''

"'found = False\nindexes = []\nfor i, l in enumerate(df_toolbar.Event.tolist() + ['ENDE']):\n    #print(i, l, found)\n    if l in 'Font FamilyFont':\n        ind = i\n        found = True\n    elif l not in 'Font FamilyFont' and found:\n        indexes.append(ind)\n        found = False\n    elif l in 'Font FamilyFont' and found:\n        indexes.append(i)\nprint(indexes)\nlen(indexes)"

In [23]:
cmd_array = sorted(df_cmd.Event.unique())
print(cmd_array)
#actions_array = ["Italic", "Bold", "Underline", "Indent", "Align", "FontSize", "FontFamily"]
actions_array = ["italic", "bold", "underline", "indent", "align", "fontSize", "fontFamily"]
toolbar_actions = [actions_array[3], actions_array[4], actions_array[4], actions_array[4], actions_array[1], actions_array[6], actions_array[5], actions_array[0], actions_array[2]]
cmd_actions = [actions_array[1], actions_array[0], actions_array[2], actions_array[3], actions_array[3]]
cmd_dict = dict(zip(cmd_array, cmd_actions))
toolbar_dict = dict(zip(toolbar_array, toolbar_actions))
print("cmd_dict\n",cmd_dict)
print("toolbar_dict\n",toolbar_dict)

['Ctrl+7', 'Ctrl+A', 'Ctrl+B', 'Ctrl+C', 'Ctrl+H', 'Ctrl+I', 'Ctrl+N', 'Ctrl+S', 'Ctrl+Tab', 'Ctrl+U', 'Ctrl+V', 'Ctrl+Y', 'Ctrl+Z', 'Esc', 'Shift+Tab', 'Tab']
cmd_dict
 {'Ctrl+7': 'bold', 'Ctrl+A': 'italic', 'Ctrl+B': 'underline', 'Ctrl+C': 'indent', 'Ctrl+H': 'indent'}
toolbar_dict
 {' undefined': 'indent', 'Align centerAlign': 'align', 'Align leftAlign': 'align', 'Align rightAlign': 'align', 'Bold (CTRL+B)Bold': 'bold', 'Font FamilyFont': 'fontFamily', 'Font SizeFont': 'fontSize', 'Italic (CTRL+I)Italic': 'italic', 'Underline (CTRL+U)Underline': 'underline'}


In [24]:
df_toolbar.Event = df_toolbar.Event.apply(lambda x: toolbar_dict[x], axis=1)

KeyError: 'Italic'

In [25]:
df_cmd.Event = df_cmd.Event.apply(lambda x: cmd_dict[x], axis=1)

KeyError: 'Tab'

In [ ]:
df_toolbar["Type"] = "Toolbar"
df_cmd["Type"] = "Cmd"
df_actions = pd.concat([df_toolbar, df_cmd])
df_actions = df_actions.sort_values(by="Timestamp")
df_actions.head()

In [ ]:
actions_array_num = np.arange(1,len(actions_array)+1)
action_dict = dict(zip(actions_array,actions_array_num))
action_dict

In [ ]:
df_actions.Event = df_actions.Event.apply(lambda x: action_dict[x])
#df_actions.reset_index(drop=True).to_pickle(study_data_path + "../ReRun/clean_data.pkl")
df_actions.reset_index(drop=True).to_pickle("clean_data.pkl")